In [ ]:
#Libs
import cv2
import numpy as np
import pandas as pd
from tabulate import tabulate
import matplotlib.pyplot as plt

# Methods

In [ ]:
def split_on_nan_row(recording):
    # Split the DataFrame into subdatasets
    subdatasets = []
    current_subdataset = []

    for index, row in recording.iterrows():
        if pd.isna(row['x1']) and pd.isna(row['y1']) and pd.isna(row['x2']) and pd.isna(row['y2']):
            if current_subdataset:
                subdatasets.append(pd.DataFrame(current_subdataset))
                current_subdataset = []
        elif pd.isna(row['x1']) and pd.isna(row['y1']) and row['x2'] and row['y2']:
            if current_subdataset:
                subdatasets.append(pd.DataFrame(current_subdataset))
                current_subdataset = []
        elif row['x1'] and row['y1'] and pd.isna(row['x2']) and pd.isna(row['y2']):
            if current_subdataset:
                subdatasets.append(pd.DataFrame(current_subdataset))
                current_subdataset = []
        else:
            if index > 0:
                prev_row = recording.iloc[index - 1]
                if not (pd.isna(prev_row['x1']) and pd.isna(prev_row['y1']) and pd.isna(prev_row['x2']) and pd.isna(prev_row['y2'])):
                    current_subdataset.append(row)

        # Append the last subdataset if it exists
    if current_subdataset:
        subdatasets.append(pd.DataFrame(current_subdataset))

    for i in range(len(subdatasets)):
        if len(subdatasets[i]) < 10:
            subdatasets.pop(i)
            break
    return subdatasets

In [ ]:
def get_average_points(subdatasets):
    average_points = []

    for i in subdatasets:
        x1 = i['x1'].mean() 
        y1 = i['y1'].mean()
        x2 = i['x2'].mean()
        y2 = i['y2'].mean()
        average_points.append((x1, y1, x2, y2))

    return average_points

In [ ]:
def correct_points_orientation(list_of_points, label):
    average_points_corrected = []
    for i in range(len(list_of_points)):
        x1, y1, x2, y2 = list_of_points[i]
        if x1 < x2:
            x1, x2 = x2, x1
            y1, y2 = y2, y1
        average_points_corrected.append((x1, y1, x2, y2, label[i]))
    return average_points_corrected

# Variables

In [ ]:
# Angular error
angle_error = np.radians(0.25)  # 0.25°

# Define the positions of the eyes  (world coordinates)
coord_left_eye = np.array([-3.25, 0, 0])
coord_right_eye = np.array([3.25, 0, 0])

# Recordings

In [ ]:
label1 = ['infini', '25c', '25up', '25r', '50c', '50up', '50r', '75c', '75up', '75r', '200c', '200up', '200r' ]

recording1_left = pd.read_csv('./recording1/centroids_left.csv')
recording1_right = pd.read_csv('./recording1/centroids_right.csv')

# Retenir seulement les images non noirs
subdatasets1_left = split_on_nan_row(recording1_left)
subdatasets1_right = split_on_nan_row(recording1_right)

# Recupérer les points moyens pour les douze points de fixations
average_points_left1 = get_average_points(subdatasets1_left)
average_points_right1 = get_average_points(subdatasets1_right)

# Verifier qu'il n'y a pas d'échanges entre les centroides 1 et 2
average_points_left_corrected1, average_points_right_corrected1 = correct_points_orientation(average_points_left1, label1), correct_points_orientation(average_points_right1, label1)

xy_eye_left1 = np.column_stack(([(average_points_left_corrected1[i][0] + average_points_left_corrected1[i][2])/2 for i in range(len(average_points_left_corrected1))], [(average_points_left_corrected1[i][1] + average_points_left_corrected1[i][3])/2 for i in range(len(average_points_left_corrected1))]))
xy_eye_right1 = np.column_stack(([(average_points_right_corrected1[i][0] + average_points_right_corrected1[i][2])/2 for i in range(len(average_points_right_corrected1))], [(average_points_right_corrected1[i][1] + average_points_right_corrected1[i][3])/2 for i in range(len(average_points_right_corrected1))]))

## Recording 2

In [ ]:
label2 = ['infini', '25c', '50c', '75c', '200c', '25up', '50up', '75up', '200up', '25r', '50r',  '75r', '200r' ]

recording2_left = pd.read_csv('./recording2/centroids_left.csv')
recording2_left = recording2_left.drop([11474])
recording2_left = recording2_left.reset_index(drop=True)

recording2_right = pd.read_csv('./.recording2/centroids_right.csv')
recording2_right = recording2_right.drop([319, 5926, 7611, 10201, 11500, 12791])
recording2_right = recording2_right.reset_index(drop=True)

subdatasets2_left = split_on_nan_row(recording2_left)
subdatasets2_right = split_on_nan_row(recording2_right)

average_points_left2 = get_average_points(subdatasets2_left)
average_points_right2 = get_average_points(subdatasets2_right)

average_points_left_corrected2, average_points_right_corrected2 = correct_points_orientation(average_points_left2, label2), correct_points_orientation(average_points_right2, label2)

xy_eye_left2 = np.column_stack(([(average_points_left_corrected2[i][0] + average_points_left_corrected2[i][2])/2 for i in range(len(average_points_left_corrected2))], [(average_points_left_corrected2[i][1] + average_points_left_corrected2[i][3])/2 for i in range(len(average_points_left_corrected2))]))
xy_eye_right2 = np.column_stack(([(average_points_right_corrected2[i][0] + average_points_right_corrected2[i][2])/2 for i in range(len(average_points_right_corrected2))], [(average_points_right_corrected2[i][1] + average_points_right_corrected2[i][3])/2 for i in range(len(average_points_right_corrected2))]))

## Recording 3

In [ ]:
label3 = ['infini', '75c', '75up', '50up', '75r', '50r', '200c', '25c', '25r', '50c', '200r', '25up', '200up']

recording3_left = pd.read_csv('./recording3/centroids_left.csv')
recording3_right = pd.read_csv('./recording3/centroids_right.csv')
recording3_right = recording3_right.drop([9268, 10181, 11001, 12687])
recording3_right = recording3_right.reset_index(drop=True)

subdatasets3_left = split_on_nan_row(recording3_left)
subdatasets3_right = split_on_nan_row(recording3_right)

average_points_left3 = get_average_points(subdatasets3_left)
average_points_right3 = get_average_points(subdatasets3_right)

average_points_left_corrected3, average_points_right_corrected3 = correct_points_orientation(average_points_left3, label3), correct_points_orientation(average_points_right3, label3)

xy_eye_left3 = np.column_stack(([(average_points_left_corrected3[i][0] + average_points_left_corrected3[i][2])/2 for i in range(len(average_points_left_corrected3))], [(average_points_left_corrected3[i][1] + average_points_left_corrected3[i][3])/2 for i in range(len(average_points_left_corrected3))]))
xy_eye_right3 = np.column_stack(([(average_points_right_corrected3[i][0] + average_points_right_corrected3[i][2])/2 for i in range(len(average_points_right_corrected3))], [(average_points_right_corrected3[i][1] + average_points_right_corrected3[i][3])/2 for i in range(len(average_points_right_corrected3))]))

## Recording 4

In [ ]:
label4 = ['infini', '25up', '200c', '200up', '75c', '25c', '50c', '200r', '25r', '75r', '75up', '50up', '50r' ]

recording4_left = pd.read_csv('./recording4/centroids_left.csv')
recording4_left = recording4_left.drop([1971,1972, 4402, 6891,7982,9011, 10229, 10434, 12390, 13182])
recording4_left = recording4_left.reset_index(drop=True)

recording4_right = pd.read_csv('./recording4/centroids_right.csv')
recording4_right = recording4_right.drop([1960, 4394, 8170, 10423, 13177])
recording4_right = recording4_right.reset_index(drop=True)

subdatasets4_left = split_on_nan_row(recording4_left)
subdatasets4_right = split_on_nan_row(recording4_right)

average_points_left4 = get_average_points(subdatasets4_left)
average_points_right4 = get_average_points(subdatasets4_right)

average_points_left_corrected4, average_points_right_corrected4 = correct_points_orientation(average_points_left4, label4), correct_points_orientation(average_points_right4, label4)

xy_eye_left4 = np.column_stack(([(average_points_left_corrected4[i][0] + average_points_left_corrected4[i][2])/2 for i in range(len(average_points_left_corrected4))], [(average_points_left_corrected4[i][1] + average_points_left_corrected4[i][3])/2 for i in range(len(average_points_left_corrected4))]))
xy_eye_right4 = np.column_stack(([(average_points_right_corrected4[i][0] + average_points_right_corrected4[i][2])/2 for i in range(len(average_points_right_corrected4))], [(average_points_right_corrected4[i][1] + average_points_right_corrected4[i][3])/2 for i in range(len(average_points_right_corrected4))]))